In [1]:
import os
import numpy as np
import pandas as pd
import librosa as lr
import librosa.display
import glob
import matplotlib.pyplot as plt
import moviepy.editor as mp
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.metrics import confusion_matrix, classification_report
from sklearn.ensemble import RandomForestClassifier
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Conv1D, MaxPooling1D, LSTM
from keras.utils import to_categorical
from keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.layers import BatchNormalization
from keras.preprocessing.sequence import TimeseriesGenerator

In [2]:
EMOTIONS = {1:'neutral', 2:'calm', 3:'happy', 4:'sad', 5:'angry', 6:'fear', 7:'disgust', 0:'surprise'}

In [3]:
data = pd.DataFrame(columns=['Emotion', 'Emotion intensity', 'Gender','Path'])

In [4]:
MFCC_LEN = 35

In [5]:
dataset = []
files = glob.glob(fr'C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\projet_dl\projet_DL\dataset\*')
for folders in files:
    folder1 = glob.glob(fr'{folders}\*')
    
    dataset.extend(folder1)
    
    print(dataset)

['C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-01-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-01-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-02-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-02-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-01-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-01-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-02-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-02-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\EC

In [6]:
print(len(dataset))

2452


In [7]:
# Définir une fonction pour extraire les caractéristiques audio
def extract_features(file_path):
    # Charger le fichier audio avec Librosa
    y, sr = lr.load(file_path, sr=None)
    
    # Calculer le spectre mél
    mel_spec = librosa.feature.melspectrogram(y=y, sr=sr)
    
    # Calculer les coefficients cepstraux en fréquence (MFCC)
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=MFCC_LEN)
    mfcc = np.mean(mfcc.T, axis=0)
    
    # Calculer le chromagramme
    chroma = librosa.feature.chroma_stft(y=y, sr=sr)
    
    # Calculer le rythme
    tempo, _ = librosa.beat.beat_track(y=y, sr=sr)

    return  mel_spec, mfcc, chroma, tempo

In [8]:
# Définir les émotions
EMOTIONS = {1: 'neutral', 2: 'calm', 3: 'happy', 4: 'sad', 5: 'angry', 6: 'fear', 7: 'disgust', 8: 'surprise'}

# Chemin du dossier contenant les fichiers audio
DATA_PATH = fr'C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\projet_dl\projet_DL\dataset'

# Définir la liste pour stocker les données
data = []

# Parcourir les dossiers
folders = glob.glob(os.path.join(DATA_PATH, '*'))
for folder in folders:
    # Parcourir les fichiers dans chaque dossier
    folder1 = glob.glob(os.path.join(folder, '*'))
    for files1 in folder1:
        data1 = glob.glob(os.path.join(files1, '*'))
        
        y, sr = lr.load(files1, sr=None)
            
        # Extraire les informations du fichier
        identifiers = os.path.basename(files1).split('.')[0].split('-')
            
        modality = int(identifiers[0])
        vocal_channel = int(identifiers[1])
        emotion = int(identifiers[2])
        emotion_intensity = int(identifiers[3])
        statement = int(identifiers[4])
        repetition = int(identifiers[5])
        actor = int(identifiers[6])
            
        # Mapping des informations pour correspondre à notre structure
        emotion_mapping = {1: 'neutral', 2: 'calm', 3: 'happy', 4: 'sad', 5: 'angry', 6: 'fear', 7: 'disgust', 8: 'surprise'}
        #emotion = emotion_mapping[emotion]
        emotion_intensity = 'normal' if emotion_intensity == 1 else 'strong'            
        gender = 'female' if actor % 2 == 0 else 'male'
            
        # Ajouter les informations au DataFrame
        data.append({
            'Modality': modality,
            'Vocal Channel': vocal_channel,
            'Emotion': emotion,
            'Emotion_string': emotion_mapping[emotion],
            'Emotion Intensity': emotion_intensity,
            'Statement': statement,
            'Repetition': repetition,
            'Actor': actor,
            'Gender': gender,
            'Path': files1
         })

# Convertir la liste en DataFrame
df = pd.DataFrame(data)

print(df)

      Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0            3              1        1        neutral            normal   
1            3              1        1        neutral            normal   
2            3              1        1        neutral            normal   
3            3              1        1        neutral            normal   
4            3              1        2           calm            normal   
...        ...            ...      ...            ...               ...   
2447         3              2        6           fear            normal   
2448         3              2        6           fear            strong   
2449         3              2        6           fear            strong   
2450         3              2        6           fear            strong   
2451         3              2        6           fear            strong   

      Statement  Repetition  Actor  Gender  \
0             1           1      1    male   
1      

In [9]:
df_copy = df.copy()
df_copy

Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0            3              1        1        neutral            normal   
1            3              1        1        neutral            normal   
2            3              1        1        neutral            normal   
3            3              1        1        neutral            normal   
4            3              1        2           calm            normal   
...        ...            ...      ...            ...               ...   
2447         3              2        6           fear            normal   
2448         3              2        6           fear            strong   
2449         3              2        6           fear            strong   
2450         3              2        6           fear            strong   
2451         3              2        6           fear            strong   

      Statement  Repetition  Actor  Gender  \
0             1           1      1    male   
1             1           2      1    male   
2             2           1      1    male   
3             2           2      1    male   
4             1           1      1    male   
...         ...         ...    ...     ...   
2447          2           2     24  female   
2448          1           1     24  female   
2449          1           2     24  female   
2450          2           1     24  female   
2451          2           2     24  female   

                                                   Path  
0     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
1     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
2     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
3     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
4     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
...                                                 ...  
2447  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
2448  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
2449  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
2450  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  
2451  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  

[2452 rows x 10 columns]

In [10]:
#
mel_spec, mfcc, chroma, tempo = extract_features(df_copy['Path'][20])

mfcc

array([-7.1587268e+02,  7.4985298e+01,  2.9195237e+00,  1.1441712e+01,
        6.9607286e+00,  1.3466071e+01, -6.7260499e+00,  4.7315598e+00,
       -6.0603504e+00, -5.0608444e+00, -7.6180463e+00, -3.5482144e+00,
       -1.2796025e+00, -3.5052683e+00,  1.5040183e+00, -1.6673055e+00,
       -4.6470814e+00, -1.3987222e+00,  4.2264077e-01, -3.0675159e+00,
       -3.5612206e+00, -3.6089151e+00, -2.3603621e+00,  1.8047141e-01,
       -3.6961973e+00, -3.8520033e+00, -1.9938285e+00, -6.1822903e-01,
       -4.4605880e+00, -2.0738494e+00, -5.5384499e-01, -2.5048208e+00,
       -2.6100931e+00, -1.6681180e+00, -9.0549302e-01], dtype=float32)

In [11]:
#
mel_spec, mfcc, chroma, tempo = extract_features(df_copy['Path'][20])

columns = [f"MFCC_{i+1}" for i in range(MFCC_LEN)]
dataftest = pd.DataFrame(columns=columns)

for index, row in dataftest.iterrows():
    # Stockez les caractéristiques résumées dans le DataFrame
    if mfcc is not None:
        df_copy.at[index, [f"MFCC_{i+1}" for i in range(MFCC_LEN)]] = mfcc

In [12]:
dataftest

Empty DataFrame
Columns: [MFCC_1, MFCC_2, MFCC_3, MFCC_4, MFCC_5, MFCC_6, MFCC_7, MFCC_8, MFCC_9, MFCC_10, MFCC_11, MFCC_12, MFCC_13, MFCC_14, MFCC_15, MFCC_16, MFCC_17, MFCC_18, MFCC_19, MFCC_20, MFCC_21, MFCC_22, MFCC_23, MFCC_24, MFCC_25, MFCC_26, MFCC_27, MFCC_28, MFCC_29, MFCC_30, MFCC_31, MFCC_32, MFCC_33, MFCC_34, MFCC_35]
Index: []

[0 rows x 35 columns]

In [13]:
for n in range(1,MFCC_LEN+1):
    df_copy[f"MFCC_{n}"] = None

df_copy.head()

Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0         3              1        1        neutral            normal   
1         3              1        1        neutral            normal   
2         3              1        1        neutral            normal   
3         3              1        1        neutral            normal   
4         3              1        2           calm            normal   

   Statement  Repetition  Actor Gender  \
0          1           1      1   male   
1          1           2      1   male   
2          2           1      1   male   
3          2           2      1   male   
4          1           1      1   male   

                                                Path  ... MFCC_26 MFCC_27  \
0  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
1  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
2  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
3  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
4  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   

  MFCC_28 MFCC_29 MFCC_30 MFCC_31 MFCC_32 MFCC_33 MFCC_34 MFCC_35  
0    None    None    None    None    None    None    None    None  
1    None    None    None    None    None    None    None    None  
2    None    None    None    None    None    None    None    None  
3    None    None    None    None    None    None    None    None  
4    None    None    None    None    None    None    None    None  

[5 rows x 45 columns]

In [14]:
columns = [f"MFCC_{i+1}" for i in range(MFCC_LEN)]
data = pd.DataFrame(columns=columns)

for index, row in df_copy.iterrows():
    file_path = row['Path']
    mel_spec, mfcc, chroma, tempo = extract_features(file_path)
    # Stockez les caractéristiques résumées dans le DataFrame
    if mfcc is not None:
        df_copy.loc[index, [f"MFCC_{i+1}" for i in range(MFCC_LEN)]] = mfcc
        df_copy.loc[index, 'Mel Spectrogram'] = mel_spec.mean()
        df_copy.loc[index, 'Chroma'] = chroma.mean()            
        df_copy.loc[index, 'Tempo'] = tempo

In [16]:
df_copy.columns

Index(['Modality', 'Vocal Channel', 'Emotion', 'Emotion_string',
       'Emotion Intensity', 'Statement', 'Repetition', 'Actor', 'Gender',
       'Path', 'MFCC_1', 'MFCC_2', 'MFCC_3', 'MFCC_4', 'MFCC_5', 'MFCC_6',
       'MFCC_7', 'MFCC_8', 'MFCC_9', 'MFCC_10', 'MFCC_11', 'MFCC_12',
       'MFCC_13', 'MFCC_14', 'MFCC_15', 'MFCC_16', 'MFCC_17', 'MFCC_18',
       'MFCC_19', 'MFCC_20', 'MFCC_21', 'MFCC_22', 'MFCC_23', 'MFCC_24',
       'MFCC_25', 'MFCC_26', 'MFCC_27', 'MFCC_28', 'MFCC_29', 'MFCC_30',
       'MFCC_31', 'MFCC_32', 'MFCC_33', 'MFCC_34', 'MFCC_35',
       'Mel Spectrogram', 'Chroma', 'Tempo'],
      dtype='object')

In [17]:
df_copy.iloc[:, -MFCC_LEN-3:]

MFCC_1     MFCC_2     MFCC_3     MFCC_4     MFCC_5     MFCC_6  \
0    -726.217224   68.54142   3.293398    12.2053   5.510278   13.66741   
1    -719.128296  70.201569   1.168397  13.122543    7.83695   14.41129   
2    -714.995728  69.689346   3.924564   11.92419   6.421723  11.011614   
3    -710.975281  67.564888   5.782241  13.230726   6.190846  12.628252   
4    -759.921753  75.783524   6.023605  14.557394   6.454188  14.631508   
...          ...        ...        ...        ...        ...        ...   
2447  -576.45282  54.380749   -7.73585  10.948718  -14.57324  -4.124824   
2448 -510.658813  58.819607 -24.300251   7.678475 -14.771711  -6.677704   
2449 -510.523682  58.066872 -20.944351  10.764229 -14.864123  -1.802712   
2450 -491.407776  53.550083  -18.45842   13.94903 -14.972725  -2.478487   
2451 -486.209534   43.12595 -17.961823  11.411658 -16.681572  -4.672381   

         MFCC_7    MFCC_8     MFCC_9    MFCC_10  ...   MFCC_29   MFCC_30  \
0     -2.983828  3.098029  -3.310813  -1.564384  ... -3.333269 -1.978465   
1      -4.11136  4.468973  -3.539367  -3.658607  ... -4.091075 -1.280043   
2     -2.878103  4.509558   -4.47611  -2.671549  ... -2.857712 -1.150795   
3     -1.675169  5.657494  -4.950634  -3.477545  ... -2.159041 -1.574821   
4     -3.004551   4.62097  -5.200016   -0.70743  ... -3.722793 -1.992164   
...         ...       ...        ...        ...  ...       ...       ...   
2447 -13.325639 -4.847116   -7.97719  -11.73325  ...  1.805656 -0.543124   
2448 -16.426004 -5.567861 -10.420625 -12.032647  ... -2.216982 -2.120693   
2449 -17.079088 -2.348416 -10.327094  -7.906415  ... -0.987653 -0.266559   
2450 -14.316654 -1.642386 -10.187863  -7.901929  ... -0.548596 -0.494096   
2451 -15.395755 -1.863798  -9.232695  -8.579366  ... -0.477864 -1.560797   

       MFCC_31   MFCC_32   MFCC_33   MFCC_34   MFCC_35 Mel Spectrogram  \
0     0.457082  -1.39911 -2.926856  0.013957 -0.490734        0.002952   
1      0.27546  -2.52147 -2.987673  0.409735 -0.484184        0.003416   
2    -0.002119 -0.909152 -3.045955 -0.373294 -0.849145        0.004721   
3    -0.403806 -1.329651 -2.513405 -0.190276 -0.645949        0.004341   
4     0.206463 -2.188582 -2.835501  0.463746 -1.019167        0.001624   
...        ...       ...       ...       ...       ...             ...   
2447 -1.381986 -0.860118  0.996583 -0.232075 -2.555824        0.037530   
2448  -0.70448 -0.161278  1.945361 -0.960401 -3.126293        0.118704   
2449 -0.338121  -0.00897  0.716546 -0.852506 -1.841365        0.126680   
2450  1.177081 -0.550828 -1.049115 -1.843452 -2.105958        0.122824   
2451  -1.47207  0.513239  1.872616 -0.231549 -2.278477        0.208337   

        Chroma       Tempo  
0     0.633091  187.500000  
1     0.629568  106.132075  
2     0.619984   82.720588  
3     0.612607   66.176471  
4     0.608243  112.500000  
...        ...         ...  
2447  0.380013  160.714286  
2448  0.384475   86.538462  
2449  0.379459  193.965517  
2450  0.393004  114.795918  
2451  0.397366  181.451613  

[2452 rows x 38 columns]

In [18]:
# Normaliser les caractéristiques
scaler = StandardScaler()
df_copy[['Mel Spectrogram', 'Chroma', 'Tempo']] = scaler.fit_transform(df_copy[['Mel Spectrogram', 'Chroma', 'Tempo']])

In [19]:
print(df_copy.head())

   Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0         3              1        1        neutral            normal   
1         3              1        1        neutral            normal   
2         3              1        1        neutral            normal   
3         3              1        1        neutral            normal   
4         3              1        2           calm            normal   

   Statement  Repetition  Actor Gender  \
0          1           1      1   male   
1          1           2      1   male   
2          2           1      1   male   
3          2           2      1   male   
4          1           1      1   male   

                                                Path  ...   MFCC_29   MFCC_30  \
0  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ... -3.333269 -1.978465   
1  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ... -4.091075 -1.280043   
2  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ... -2.857712 -1.

In [20]:
# Convertir les étiquettes d'émotion en encodage one-hot
le = LabelEncoder()
df_copy['Emotion'] = le.fit_transform(df_copy['Emotion'])
y = to_categorical(df_copy['Emotion'], len(EMOTIONS))

# Séparer les données en ensembles d'entraînement et de test
X_train, X_test, y_train, y_test = train_test_split(df_copy.iloc[:, -MFCC_LEN-3:], y, test_size=0.2, random_state=42)

In [21]:
X_train = X_train.astype('float32')
y_train = y_train.astype('float32')
X_test = X_test.astype('float32')

In [22]:
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)

(1961, 38) (491, 38) (1961, 8) (491, 8)


In [29]:
# Définir le modèle
model = Sequential()
early_stopping = EarlyStopping(patience=15, restore_best_weights=True)
model_checkpoint = ModelCheckpoint('best_model_weights.h5', save_best_only=True)

#add cnn model
model.add(Conv1D(32, 5, padding='same', input_shape=(X_train.shape[1],1)))
model.add(Conv1D(32, 5, padding='same'))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(Dropout(0.3))
model.add(BatchNormalization())

model.add(Conv1D(64, 3, padding='same'))
model.add(Conv1D(64, 3, padding='same'))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(Dropout(0.3))
model.add(BatchNormalization())

# Ajouter une couche LSTM
model.add(LSTM(64, return_sequences=True))
model.add(Dropout(0.3))
model.add(LSTM(32, return_sequences=True))
model.add(Dropout(0.3))

model.add(Flatten())
model.add(Dense(256, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(len(EMOTIONS), activation='softmax'))

# Compiler le modèle
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Entraîner le modèle
model.fit(X_train, y_train, epochs=110, batch_size=64, validation_split=0.2, verbose=1, callbacks=[early_stopping, model_checkpoint])

# Prédire sur l'ensemble de test
y_pred = model.predict(X_test)
y_pred_labels = np.argmax(y_pred, axis=1)
y_test_labels = np.argmax(y_test, axis=1)

Epoch 1/110
25/25 [==============================] - 6s 53ms/step - loss: 2.0567 - accuracy: 0.1518 - val_loss: 2.0511 - val_accuracy: 0.1170
Epoch 2/110
25/25 [==============================] - 0s 16ms/step - loss: 2.0199 - accuracy: 0.1881 - val_loss: 2.0519 - val_accuracy: 0.1374
Epoch 3/110
25/25 [==============================] - 0s 17ms/step - loss: 1.9773 - accuracy: 0.2341 - val_loss: 2.1127 - val_accuracy: 0.1247
Epoch 4/110
25/25 [==============================] - 0s 16ms/step - loss: 1.9081 - accuracy: 0.2404 - val_loss: 2.2019 - val_accuracy: 0.1374
Epoch 5/110
25/25 [==============================] - 0s 18ms/step - loss: 1.8558 - accuracy: 0.2672 - val_loss: 1.8369 - val_accuracy: 0.2697
Epoch 6/110
25/25 [==============================] - 0s 17ms/step - loss: 1.8372 - accuracy: 0.2755 - val_loss: 1.7664 - val_accuracy: 0.2977
Epoch 7/110
25/25 [==============================] - 0s 18ms/step - loss: 1.8120 - accuracy: 0.2946 - val_loss: 1.7489 - val_accuracy: 0.3079
Epoch 

In [30]:
print(model.summary())

Model: "sequential_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_20 (Conv1D)          (None, 38, 32)            192       
                                                                 
 conv1d_21 (Conv1D)          (None, 38, 32)            5152      
                                                                 
 max_pooling1d_10 (MaxPooli  (None, 19, 32)            0         
 ng1D)                                                           
                                                                 
 dropout_25 (Dropout)        (None, 19, 32)            0         
                                                                 
 batch_normalization_10 (Ba  (None, 19, 32)            128       
 tchNormalization)                                               
                                                                 
 conv1d_22 (Conv1D)          (None, 19, 64)           